In [2]:
import pandas as pd
import json
from pathlib import Path
from utils import sanitize_names
from taxonomy import get_lineage
import pprint

In [3]:
def create_virus_metadata(virus_dir: Path):
    metadata_json = virus_dir.joinpath('virus.json')
    with metadata_json.open() as mj:
        virus_metadata = sanitize_names(json.load(mj), virus=True)
    return virus_metadata


def create_host_metadata(host_dir: Path):
    metadata_json = host_dir.joinpath('host.json')
    with metadata_json.open() as mj:
        host_metadata = sanitize_names(json.load(mj), virus=False)
    return host_metadata


def create_dict_by_rank(data, rank_to_search):
    result_dict = {}

    # for key in data:
    #     temp = get_lineage(data[key], 'lineage_names')
    #     key
    
    for item in data.values():
        temp = get_lineage(item, 'lineage_names')
        item['lineage_names'] = list(temp.values())
        rank_list = item['lineage_ranks']
        name_list = item['lineage_names']

        if rank_to_search in rank_list:
            rank_index = rank_list.index(rank_to_search)
            rank_name_dict = dict(zip(rank_list, name_list))
            # rank_name_dict = get_lineage(item, 'lineage_names')
            result_dict[name_list[rank_index]] = rank_name_dict
        
    return result_dict


# this can be better just in case - more flexible
def test(col, master_virus_dict, tax_level, map_dict=None):
    sorted_col = col.sort_values(ascending=False)[:5]
    print(sorted_col.name)
    print(sorted_col.index)
    lineage = get_lineage(master_virus_dict[sorted_col.name]['host'], 'lineage_names')
    print(lineage)
    if map_dict is None:
        sub_df = {f'top{i + 1}': 1 if lineage[tax_level] in sorted_col.index[:i + 1] else 0 for i, name in enumerate(sorted_col.index)}
        print(sub_df)
        return sub_df
    
    sorted_col.index = [map_dict[x][tax_level] for x in sorted_col.index]
    sub_df = {f'top{i + 1}': 1 if lineage[tax_level] in sorted_col.index[:i + 1] else 0 for i, name in enumerate(sorted_col.index)}
    print(sub_df)
    return sub_df


def distribution(col, master_virus_dict, tax_level, map_dict=None):
    sorted_col = col.sort_values(ascending=False)[:1]
    print(sorted_col.name)
    print(sorted_col.index)
    lineage = get_lineage(master_virus_dict[sorted_col.name]['host'], 'lineage_names')
    print(lineage)
    if map_dict is None:
        sub_df = {lineage[tax_level]: 1 if lineage[tax_level] in sorted_col.index[:i + 1] else 0 for i, name in enumerate(sorted_col.index)}
        print(sub_df)
        return sub_df
    
    sorted_col.index = [map_dict[x][tax_level] for x in sorted_col.index]
    sub_df = {lineage[tax_level]: 1 if lineage[tax_level] in sorted_col.index[:i + 1] else 0 for i, name in enumerate(sorted_col.index)}
    print(sub_df)
    return sub_df


def distribution_nocheck(col, master_virus_dict, tax_level, map_dict=None):
    sorted_col = col.sort_values(ascending=False)[:1]
    print(sorted_col.name)
    print(sorted_col.index)
    lineage = get_lineage(master_virus_dict[sorted_col.name]['host'], 'lineage_names')
    print(lineage)
    if map_dict is None:
        sub_df = {lineage[tax_level]: 1 if lineage[tax_level] in sorted_col.index[:i + 1] else 0 for i, name in enumerate(sorted_col.index)}
        print(sub_df)
        return sub_df
    
    sorted_col.index = [map_dict[x][tax_level] for x in sorted_col.index]
    sub_df = {sorted_col.index[:i + 1][0]: 1 for i, name in enumerate(sorted_col.index)}
    print(sub_df)
    return sub_df


In [39]:
meta_vir = create_virus_metadata(Path('X:/edwards2016/virus/'))
meta_host = create_host_metadata(Path('X:/edwards2016/host/'))
df = pd.read_csv('../phdna_proper_opt/species_noise_04-07-2023/predictions.csv', index_col=0)
df = pd.read_csv('../phdna_proper_opt/fam_noise_05-07-2023.best_classifier/predictions.csv', index_col=0)
df.fillna(0, inplace=True)
# set type of float for all columns     
# df = df.astype(float)
print(len(df.columns))
# get top 5 rows from each column - each column is sorted descending value  
# top_5 = df.apply(lambda x: x.sort_values(ascending=False))
map_dict = create_dict_by_rank(meta_host, 'family')
print(map_dict)
pprint.pprint(meta_vir)
top_5 = df.apply(test, args=(meta_vir, 'species', None))
dist = df.apply(distribution, args=(meta_vir, 'class', map_dict))
dist_nocheck = df.apply(distribution_nocheck, args=(meta_vir, 'class', map_dict))
df_top_5 = pd.DataFrame(top_5.to_list(), index=top_5.index).T
df_dist = pd.DataFrame(dist.to_list(), index=dist.index).T
df_dist_nocheck = pd.DataFrame(dist_nocheck.to_list(), index=dist_nocheck.index).T
df_top_5['correct'] = df_top_5.sum(axis=1)
df_top_5['correct_percent'] = df_top_5['correct'] / len(df.columns)
df_dist['all'] = df_dist.count(axis=1)
df_dist['all_dist'] = (df_dist['all'] / df_dist['all'].sum(axis=0)) * 100
df_dist_nocheck_counts = df_dist_nocheck.count(axis=1).to_frame()
df_dist_nocheck_counts.columns = ['all_predicted']
df_dist = pd.concat([df_dist, df_dist_nocheck_counts], axis=1)
df_dist['all_predicted_dist'] = (df_dist['all_predicted'] / df_dist['all_predicted'].sum(axis=0)) * 100
df_dist['correct'] = df_dist.loc[:, df_dist.columns != "all"].apply(lambda row: sum(row == 1), axis=1)
df_dist['correct_dist'] = (df_dist['correct'] / df_dist['all'].sum(axis=0)) * 100
df_dist['correct_percent'] = (df_dist['correct'] / df_dist['all']) * 100
print(df_top_5['correct_percent'])
# print(top_5)
# print(df)
# df.set_index('index', inplace=True)

820
{'Xanthomonadaceae': {'superkingdom': 'Bacteria', 'phylum': 'Proteobacteria', 'class': 'Gammaproteobacteria', 'order': 'Xanthomonadales', 'family': 'Xanthomonadaceae', 'genus': 'Xanthomonas', 'species': 'Xanthomonas euvesicatoria'}, 'Acholeplasmataceae': {'superkingdom': 'Bacteria', 'phylum': 'Tenericutes', 'class': 'Mollicutes', 'order': 'Acholeplasmatales', 'family': 'Acholeplasmataceae', 'genus': 'Candidatus Phytoplasma', 'species': 'Candidatus Phytoplasma australiense'}, 'Enterobacteriaceae': {'superkingdom': 'Bacteria', 'phylum': 'Proteobacteria', 'class': 'Gammaproteobacteria', 'order': 'Enterobacteriales', 'family': 'Enterobacteriaceae', 'genus': 'Candidatus Blochmannia', 'species': 'Candidatus Blochmannia pennsylvanicus'}, 'Erythrobacteraceae': {'superkingdom': 'Bacteria', 'phylum': 'Proteobacteria', 'class': 'Alphaproteobacteria', 'order': 'Sphingomonadales', 'family': 'Erythrobacteraceae', 'genus': 'Erythrobacter', 'species': 'Erythrobacter litoralis'}, 'Listeriaceae': {'

In [40]:
import seaborn as sns
import matplotlib.pyplot as plt
import numpy as np
import plotly.express as px

crashes = sns.load_dataset("car_crashes").sort_values("total", ascending=False)
tips = px.data.tips()
df_dist = df_dist.reset_index().rename(columns={'index': 'class'})
df_melted = df_dist.melt(id_vars='class', value_vars=['all_dist', 'all_predicted_dist', 'correct_dist'], var_name='dist_type', value_name='percentage')
fig = px.bar(df_melted, x="percentage", y="dist_type", color='class', orientation='h', text='percentage', text_auto='.3f',
             height=800,
             width=1200,
             title='Distrybucja klas gospodarza w przewidywaniach',
             template='seaborn',
             labels={"percentage":"% przewidywań", "dist_type":"Typ dystrybucji", "class":"Klasy"}
             )
fig.update_traces(textposition='inside')
fig.update_layout(
    font_family="Roboto"
)
fig.show()


In [52]:
pprint.pprint(meta_host)

{'NC_000117': {'lineage_names': ['Bacteria',
                                 'Chlamydiae',
                                 'Chlamydiia',
                                 'Chlamydiales',
                                 'Chlamydiaceae',
                                 'Chlamydia',
                                 'Chlamydia trachomatis'],
               'lineage_ranks': ['superkingdom',
                                 'phylum',
                                 'class',
                                 'order',
                                 'family',
                                 'genus',
                                 'species'],
               'organism_name': 'Chlamydia trachomatis D/UW-3/CX',
               'taxid': '272561',
               'version': 'NC_000117.1'},
 'NC_000853': {'lineage_names': ['Bacteria',
                                 'Thermotogae',
                                 'Thermotogae',
                                 'Thermotogales',
                 

In [7]:
import os


meta_vir = create_virus_metadata(Path('X:/edwards2016/virus/'))
meta_host = create_host_metadata(Path('X:/edwards2016/host/'))


def parse_json(path):
    data = json.load(open(path, encoding="utf8"))
    data_top5 = {k: [meta_host[values[0]]['lineage_names'][-1] for values in v[:5]] for k, v in data.items()}
    return data_top5


# def check_preds(col, master_virus_dict, tax_level, map_dict=None):
#     # sorted_col = col.sort_values(ascending=False)[:5]
#     # print(sorted_col.name)
#     # print(sorted_col.index)
#     lineage = get_lineage(master_virus_dict[sorted_col.name]['host'], 'lineage_names')
#     print(lineage)
#     if map_dict is None:
#         sub_df = {f'top{i + 1}': 1 if lineage[tax_level] in sorted_col.index[:i + 1] else 0 for i, name in enumerate(sorted_col.index)}
#         print(sub_df)
#         return sub_df
    
#     sorted_col.index = [map_dict[x][tax_level] for x in sorted_col.index]
#     sub_df = {f'top{i + 1}': 1 if lineage[tax_level] in sorted_col.index[:i + 1] else 0 for i, name in enumerate(sorted_col.index)}
#     print(sub_df)
#     return sub_df

files = [f for f in Path('../phdna_proper_opt/comparison_src/').iterdir()]
master = {f.stem: parse_json(f.as_posix()) for f in files}
print(files)
print(master.keys())
# piler_df = pd.read_json('../phdna_proper_opt/comparison/pilercr-2mismatches.json')

[WindowsPath('../phdna_proper_opt/comparison_src/blastn.json'), WindowsPath('../phdna_proper_opt/comparison_src/k6-kendalltau.json'), WindowsPath('../phdna_proper_opt/comparison_src/k6-manhattan_distance.json'), WindowsPath('../phdna_proper_opt/comparison_src/mash-k21.json'), WindowsPath('../phdna_proper_opt/comparison_src/pilercr-2mismatches.json'), WindowsPath('../phdna_proper_opt/comparison_src/virhostmatcher.json'), WindowsPath('../phdna_proper_opt/comparison_src/wish.json')]
dict_keys(['blastn', 'k6-kendalltau', 'k6-manhattan_distance', 'mash-k21', 'pilercr-2mismatches', 'virhostmatcher', 'wish'])


In [8]:
# pprint.pprint(master['wish'])
pprint.pprint(master['pilercr-2mismatches'])
# df_p = pd.DataFrame.from_dict(master['pilercr-2mismatches'])
# pprint.pprint(master['pilercr-2mismatches'])
df = pd.read_csv('../phdna_proper_opt/species_noise_04-07-2023/predictions.csv', index_col=0)
df.fillna(0, inplace=True)
top_5 = df.apply(test, args=(meta_vir, 'species', None))
df_top_5 = pd.DataFrame(top_5.to_list(), index=top_5.index).T
df_top_5['correct'] = df_top_5.sum(axis=1)
df_top_5['correct_percent'] = df_top_5['correct'] / len(df.columns) * 100
df_top_5['tool'] = 'phastDNA'

def make_preds_df(tool, tax_level):
    out_preds = {}
    for k, v in master[tool].items():
        lineage = get_lineage(meta_vir[k]['host'], 'lineage_names')
        preds = [1 if lineage[tax_level] in v[:i + 1] else 0 for i, val in enumerate(v)]
        if len(preds) < 5:
            if preds:
                preds.extend([preds[-1]] * (5 - len(preds)))
            else:
                preds.extend([0] * 5)
        out_preds[k] = preds
    out_df = pd.DataFrame(out_preds, index=[f'top{x + 1}' for x in range(5)])
    out_df['correct'] = out_df.sum(axis=1)
    out_df['correct_percent'] = out_df['correct'] / len(df.columns) * 100
    out_df['tool'] = tool
    return out_df

dfs_tools = [make_preds_df(tool, 'species') for tool in master.keys()]
dfs_tools.append(df_top_5)
df_tools = pd.concat(dfs_tools)
df_tools.reset_index(inplace=True)
df_tools = df_tools.sort_values(['tool', 'correct_percent'], ascending=True)
fig = px.line(df_tools, 
              x='index', 
              y='correct_percent', 
              color='tool', 
              markers=True, 
              template='seaborn',
              title="Najlepsze poprawne przewidywania dla gatunku",
              height=500,
              width=700,
              labels={
                     "index": "N najlepszych poprawnych przewidywań",
                     "correct_percent": "% poprawnych przewidywań",
                     "tool": "Narzędzie"
                 })
fig.update_layout(
    font_family="Roboto"
)
fig.show()
fig.write_image('../phdna_proper_opt/comparison_out/comparison_topN.png', scale=2)
# pprint.pprint(piler_preds)
# df_piler = pd.DataFrame(piler_preds, index=[f'top_{x + 1}' for x in range(5)])
# piler_preds = {k: [0 if get_lineage(meta_vir[k]['host'], 'lineage_names')['species'] in val for val in v]  for k, v in master['pilercr-2mismatches']}


{'NC_000866': [],
 'NC_000871': ['Streptococcus thermophilus',
               'Streptococcus thermophilus',
               'Streptococcus thermophilus',
               'Streptococcus thermophilus',
               'Streptococcus thermophilus'],
 'NC_000872': ['Streptococcus thermophilus',
               'Streptococcus thermophilus',
               'Streptococcus thermophilus',
               'Streptococcus thermophilus',
               'Streptococcus thermophilus'],
 'NC_000896': [],
 'NC_000902': [],
 'NC_000924': [],
 'NC_000929': [],
 'NC_001271': [],
 'NC_001330': [],
 'NC_001331': ['Pseudomonas aeruginosa'],
 'NC_001332': [],
 'NC_001341': [],
 'NC_001396': [],
 'NC_001416': [],
 'NC_001417': [],
 'NC_001418': [],
 'NC_001420': [],
 'NC_001421': [],
 'NC_001422': [],
 'NC_001426': [],
 'NC_001447': [],
 'NC_001604': [],
 'NC_001609': [],
 'NC_001628': [],
 'NC_001697': [],
 'NC_001706': [],
 'NC_001741': [],
 'NC_001825': [],
 'NC_001835': [],
 'NC_001884': [],
 'NC_001890': [],
 '

C:\Users\Maciej\AppData\Local\Temp\ipykernel_22644\341095367.py:33: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`



In [37]:
import matplotlib.pyplot as plt
import itertools
import seaborn as sns
import matplotlib.backends.backend_pdf as bpdf


df_summary_species = pd.read_excel('../phdna_proper_opt/summary/PhastDNA2023_Summary.xlsx', sheet_name="species_noise_2", nrows=41)
df_summary_species = df_summary_species.rename(columns={"Unnamed: 0": "iteration"})
df_summary_species.drop(columns=["-log10 lr"], inplace=True)
hypers = {
    #'epochs': (75, 500), 200
    #'vector_size': (80, 300), 180
    'frag_len': (200, 2000),
    'lr': (0.005, 0.75),
    'lr_update': (50, 500),
    'maxn': (6, 11),
    'minn': (4, 9),
    'noise': (100, 20000)
}
df_summary_species = df_summary_species.loc[:, [*hypers.keys(), 'accordance']]

cp = sns.color_palette("crest", as_cmap=True)
plt.rc('font', size=12)
plt.rc('axes', titlesize=14)
plt.rc('axes', labelsize=12)
plt.rc('xtick', labelsize=10)
plt.rc('ytick', labelsize=10)
sns.set(rc={'figure.figsize':(10,7)})
print(df_summary_species.columns[:-1])
combs = list(itertools.combinations(df_summary_species.columns[:-1], 2))
# fig, axs = plt.subplots(len(combs), figsize=(len(combs), len(combs)))
with bpdf.PdfPages('../phdna_proper_opt/summary/species_noise_2-opt.pdf') as pdf:
    for i, item in enumerate(combs):
        print(combs)
        # print(i, x, y)
        x = item[0]
        y = item[1]
        # ax = axs[i // 2, i % 2]
        # g = sns.JointGrid(data=df, x=x, y=y, space=0,
        #                 xlim=hypers[x],
        #                 ylim=hypers[y])
        # x_best = list(df.loc[df['target'] >= 70, x].iloc)
        # y_best = list(df.loc[df['target'] >= 70, y].iloc)
        # best_value = list(df.loc[df['target'] >= 70, 'target'])
        # # print(best_value)
        # g.ax_joint.scatter(x=x_best, y=y_best, c='red', alpha=0.6)
        # # g.plot_joint(sns.scatterplot, x=x_best, y=y_best, color='red', alpha=0.6, marker='+')
        # for (x_val, y_val, best) in zip(x_best, y_best, best_value):
        #     g.ax_joint.annotate(f'{best}', (x_val, y_val),
        #                         xytext=(5, 10), textcoords='offset points',
        #                         fontsize=10, color='green', ha='left', va='top')
        # sns.kdeplot(data=df, x=x, y=y, fill=True, cmap="rocket", ax=g.ax_joint, alpha=0.5, levels=45, thresh=0.05)
        # g.plot_marginals(sns.histplot, color="#03051A", alpha=1)
        # g.set_axis_labels(xlabel=x, ylabel=y, fontsize=12)
        # cp = sns.color_palette("Spectral", as_cmap=True)
        # sns.scatterplot(data=df, x=x, y=y, hue='target', alpha=0.6, palette=cp)
        df_summary_species['above_66'] = df_summary_species['accordance'] >= 0.66
        markers = {False: 'o', True: 'v'}
        sns.scatterplot(data=df_summary_species, x=x, y=y, hue='accordance', alpha=1, style="above_66", markers=markers, palette=cp)
        above_70 = df_summary_species[df_summary_species['accordance'] > 0.66]
        # for j, point in above_70.iterrows():
        #     ax.text(point[x]+0.1, point[y]+0.1, str(point['target']))
        ax = sns.kdeplot(data=df_summary_species, x=x, y=y, fill=True, cmap="rocket", alpha=0.5, levels=45, thresh=0.05, warn_singular=False)
        ax.set_xlim(hypers[x])
        ax.set_ylim(hypers[y])
        ax.set_xlabel(x)
        ax.set_ylabel(y)

        ax.legend(loc='center left', bbox_to_anchor=(1.05, 0.5))
        # axs[i].set_xlim(hypers[x])
        # axs[i].set_ylim(hypers[y])
        # axs[i].set_xlabel(x)
        # axs[i].set_ylabel(y)
        # plt.show()
        # axs[i].imshow(g.ax_joint.collections[0].get_array().reshape(45, 45).T, origin='lower', extent=g.ax_joint.get_xlim() + g.ax_joint.get_ylim(), cmap="rocket", alpha=0.5)
        # axs[i].hist2d(x_best, y_best, bins=20, alpha=0.6, cmap="rocket")
        # axs[i].set_xlim(hypers[x])
        # axs[i].set_ylim(hypers[y])
        # axs[i].set_xlabel(x)
        # axs[i].set_ylabel(y)
    # plt.tight_layout()
        plt.tight_layout()
        pdf.savefig()
        plt.close()
        # plt.show()

Index(['frag_len', 'lr', 'lr_update', 'maxn', 'minn', 'noise'], dtype='object')
[('frag_len', 'lr'), ('frag_len', 'lr_update'), ('frag_len', 'maxn'), ('frag_len', 'minn'), ('frag_len', 'noise'), ('lr', 'lr_update'), ('lr', 'maxn'), ('lr', 'minn'), ('lr', 'noise'), ('lr_update', 'maxn'), ('lr_update', 'minn'), ('lr_update', 'noise'), ('maxn', 'minn'), ('maxn', 'noise'), ('minn', 'noise')]
[('frag_len', 'lr'), ('frag_len', 'lr_update'), ('frag_len', 'maxn'), ('frag_len', 'minn'), ('frag_len', 'noise'), ('lr', 'lr_update'), ('lr', 'maxn'), ('lr', 'minn'), ('lr', 'noise'), ('lr_update', 'maxn'), ('lr_update', 'minn'), ('lr_update', 'noise'), ('maxn', 'minn'), ('maxn', 'noise'), ('minn', 'noise')]
[('frag_len', 'lr'), ('frag_len', 'lr_update'), ('frag_len', 'maxn'), ('frag_len', 'minn'), ('frag_len', 'noise'), ('lr', 'lr_update'), ('lr', 'maxn'), ('lr', 'minn'), ('lr', 'noise'), ('lr_update', 'maxn'), ('lr_update', 'minn'), ('lr_update', 'noise'), ('maxn', 'minn'), ('maxn', 'noise'), ('minn

In [96]:
import pickle
import pathlib

temp = pathlib.PosixPath
pathlib.PosixPath = pathlib.WindowsPath

# load pickle file  
with open('../phdna_proper_opt/fam_noise_05-07-2023.best_classifier/classifier.pkl', 'rb') as f:
    classifier = pickle.load(f)
pathlib.PosixPath = temp
path = pathlib.Path('../phdna_proper_opt/fam_noise_05-07-2023.best_classifier_path_correct/classifier.pkl')
path.parent.mkdir(exist_ok=True, parents=True)
classifier.model = pathlib.PosixPath("/model.n8-7.lr0.49120-162.28460.d100.no2399.fl1213.e40.losoftmax.sa100.bin")
print(classifier.model)

# save pickle to file   
with open(path, 'wb') as f:
    pickle.dump(classifier, f)

\model.n8-7.lr0.49120-162.28460.d100.no2399.fl1213.e40.losoftmax.sa100.bin
